# <font color='blue'>CMPE-297 Project Part B - Short Answer Extraction</font>

# Aaron Choi, Nelson Paz
### 1. Read CMU QA Corpus 
- QAanswerFiles.zip (found in Canvas)
- question_answer_pairs-combined.txt

#### Implement precision, recall and F1 score.
Rank all documents for a given query and return the top N documents (let's call this return set size)
Report your precision, recall and F1 for the whole CMU QA corpus for what you think is a good set of preprocessing steps and return set size.

In [22]:
# Importing Primary Libraries
from nltk.tokenize import sent_tokenize,word_tokenize
from nltk.tag import pos_tag
from nltk import ne_chunk
import glob
import math
import os
from nltk.stem import WordNetLemmatizer
import json
import codecs
from nltk.tree import Tree
from nltk.corpus import stopwords
from nltk.tokenize import RegexpTokenizer
import spacy
from heapq import nlargest 
from nltk.corpus import wordnet as wn
import string
import re
import pandas as pd
import numpy as np
nlp = spacy.load('en_core_web_lg')

# Extraction Functions 

In [23]:
# Extractions Words
def extracWords(text,fname=""):
    stopWords = set(stopwords.words('english'))
    words = []
    doc = nlp(text)
    for token in doc:
        words.append(token.text)
    nonStopSentence = [w for w in words if not w in stopWords] 
    return(nonStopSentence)

# Lemmanizing:
def extracLemma(text):
    lemmaWords =[]
    doc = nlp(text)
    for token in doc:
        lemmaWords.append(token.lemma_)
    return(lemmaWords)

# Named Entity Recognition: 
def extracNER(text):
    NER_list = []
    doc = nlp(text)
    for token in doc.ents:
            NER_list.append(token.text+"_"+token.label_)
    return(NER_list)

# Extraction By Parsing Tree:
def extracParseTree(text):
    parseTree = []
    doc =nlp(text)
    for token in doc:
        parseTree.append(str(token.text+"_"+token.dep_))
    return(parseTree)

# Extracting Positions 
def extracPos(text):
    POS_list = []
    doc = nlp(text)
    for token in doc:
        POS_list.append(str(token.text+'_'+token.tag_))
    return POS_list

In [24]:
# Relation Extraction From Wordnet
def extracRelations(wordScore):
    wordRelationsFeature = {}
    for key in wordScore:
        syn = wn.synsets(key)
        r_j = []
        if len(syn) != 0:
            for s in syn:
                synonyms = s.lemma_names()
                definition = s.definition()
                hyponyms = sorted([lemma.name() for synset in s.hyponyms() for lemma in synset.lemmas()])
                hypernyms = [lemma.name() for synset in  s.hypernyms() for lemma in synset.lemmas()]
                meronyms = s.part_meronyms()
                holonyms = s.part_holonyms()
                r_j.append({'synset':s,'relations':{'def':definition,'syn':synonyms,
                                'hypo':hyponyms,'hyper':hypernyms,'mero':meronyms,'holo':holonyms}})
        else:
            wordRelationsFeature[key] = []
        wordRelationsFeature[key] = r_j         
    return wordRelationsFeature 

# Pulling all 150 documenst text.   

In [25]:
from nltk.tokenize import sent_tokenize
import time

path = input("Enter Path to the /QAanwerFiles folder" )  # Or Press ENTER if Path is edited below. 
if path == "":
    path = 'C:/Users/Admin/CMPE_297_NLP_FinalProject/QAanswerFiles/' # The PATH to the Folder can be Edited HERE. 
ResutsPath = path
print(path)

Enter Path to the /QAanwerFiles folder
C:/Users/Admin/CMPE_297_NLP_FinalProject/QAanswerFiles/


In [6]:
start = time.time()
MainDataText = []
MainCorpusLemma =[]
e = ['S10','S09','S08']

for X in range(0,3):
    SXX = str(e[X])
    path_A = path + SXX +'/data/'
    for i in range(1,(7-X)):
        path_B = (path_A+'set'+str(i)+'/')
        os.chdir(path_B)
        for filename in glob.glob("*.txt.clean"):
            sentences=[]
            doc = {}
            f = codecs.open(filename,'r','ISO-8859-1')
            file = f.read()
            print("Document Processing ------------> ",filename)   
            for l in sent_tokenize(file):
                if l.strip():
                    w_j_obj= extracWords(l,filename)
                    l_j_obj= extracLemma(l)
                    sentences.append({"sentence":l,"lemma":l_j_obj})
                    MainCorpusLemma.extend(l_j_obj)
            doc = {'doc':filename,'sentences':sentences}
            print("Number of Lines in Document ----> ",len(sent_tokenize(file)))
            MainDataText.append(doc)

seconds = time.time() - start
print('Time Taken:', time.strftime("%H:%M:%S",time.gmtime(seconds)))

Document Processing ------------>  a1.txt.clean
Number of Lines in Document ---->  394
Document Processing ------------>  a10.txt.clean
Number of Lines in Document ---->  230
Document Processing ------------>  a2.txt.clean
Number of Lines in Document ---->  276
Document Processing ------------>  a3.txt.clean
Number of Lines in Document ---->  110
Document Processing ------------>  a4.txt.clean
Number of Lines in Document ---->  254
Document Processing ------------>  a5.txt.clean
Number of Lines in Document ---->  115
Document Processing ------------>  a6.txt.clean
Number of Lines in Document ---->  345
Document Processing ------------>  a7.txt.clean
Number of Lines in Document ---->  74
Document Processing ------------>  a8.txt.clean
Number of Lines in Document ---->  54
Document Processing ------------>  a9.txt.clean
Number of Lines in Document ---->  152
Document Processing ------------>  a1.txt.clean
Number of Lines in Document ---->  250
Document Processing ------------>  a10.txt.c

Number of Lines in Document ---->  246
Document Processing ------------>  a5.txt.clean
Number of Lines in Document ---->  15
Document Processing ------------>  a6.txt.clean
Number of Lines in Document ---->  41
Document Processing ------------>  a7.txt.clean
Number of Lines in Document ---->  159
Document Processing ------------>  a8.txt.clean
Number of Lines in Document ---->  56
Document Processing ------------>  a9.txt.clean
Number of Lines in Document ---->  22
Document Processing ------------>  a1.txt.clean
Number of Lines in Document ---->  302
Document Processing ------------>  a10.txt.clean
Number of Lines in Document ---->  363
Document Processing ------------>  a2.txt.clean
Number of Lines in Document ---->  385
Document Processing ------------>  a3.txt.clean
Number of Lines in Document ---->  236
Document Processing ------------>  a4.txt.clean
Number of Lines in Document ---->  255
Document Processing ------------>  a5.txt.clean
Number of Lines in Document ---->  226
Documen

In [15]:
# Saving the Pulling Data in the Main Folder undder a folder called "PullingResults". 

os.chdir(path)
try:
    os.mkdir('PullingResults')
except:
    print("Directory Already Exists")
    
with open('PullingResults/MainCorpus.json', 'w') as MainCopusFile:  
    json.dump(MainDataText, MainCopusFile)
print("Corpus File path -> "+path+'PullingResults/MainCorpus.json')

Directory Already Exists
Corpus File path -> C:/Users/Admin/CMPE_297_NLP_FinalProject/QAanswerFiles/PullingResults/MainCorpus.json


In [16]:
# Leminized DataFrame of all Documents, 
data_df = pd.read_json(path+ 'PullingResults/MainCorpus.json', orient='records')   
from pandas import option_context
with option_context('display.max_colwidth', 200):
    display((data_df[1:5]))

Doc  \
1  a10.txt.clean   
2   a2.txt.clean   
3   a3.txt.clean   
4   a4.txt.clean   

                                                                                                                                                                                                 Sentences  
1  [{'Sentence': 'Octopus



The octopus is a cephalopod of the order Octopoda.', 'Lemma': ['octopus', '



', 'the', 'octopus', 'be', 'a', 'cephalopod', 'of', 'the', 'order', 'Octopoda', '.']}, {'Se...  
2  [{'Sentence': 'Cougar



The cougar (Puma concolor), also known as puma, mountain lion, mountain cat, catamount or panther, depending on the region, is a mammal of the family Felidae, native to th...  
3  [{'Sentence': 'Koala



The koala (Phascolarctos cinereus) is a thickset arboreal marsupial herbivore native to Australia, and the only extant representative of the family Phascolarctidae.', 'Lemm...  
4  [{'Sentence': 'Giant_Panda



The Giant Panda (Ailuropoda melanoleuca, literally meaning "cat-foot black-and-white") is a mammal native to central-western and south western China.', 'Lemma': ['gia...

# Fetching Lemmas Relations

In [18]:
uniqueLemmas = set(MainCorpusLemma)
print('There are:',len(uniqueLemmas),'Unique Lemmas')
uniqueWordRelations = extracRelations(uniqueLemmas)
print('and',len(uniqueWordRelations),'Unique Words Relationtions')

There are: 43518 Unique Lemmas
and 43518 Unique Words Relationtions


In [21]:
# Printing Lemmas Set per a specific document. 
print(uniqueWordRelations['leopard'])

[{'synset': Synset('leopard.n.01'), 'relations': {'def': 'the pelt of a leopard', 'syn': ['leopard'], 'hypo': [], 'hyper': ['fur', 'pelt'], 'mero': [], 'holo': []}}, {'synset': Synset('leopard.n.02'), 'relations': {'def': 'large feline of African and Asian forests usually having a tawny coat with black spots', 'syn': ['leopard', 'Panthera_pardus'], 'hypo': ['leopardess', 'panther'], 'hyper': ['big_cat', 'cat'], 'mero': [], 'holo': []}}]


---------------------------------------

______________________________

# TF-IDF Computing on all 150 Documents:

In [26]:
path = input("Enter Path to the /QAanwerFiles folder" )  # Or Press ENTER if Path is edited below. 
if path == "":
    path = 'C:/Users/Admin/CMPE_297_NLP_FinalProject/QAanswerFiles/' # The PATH to the Folder can be Edited HERE. 
ResutsPath = path
print(path)

Enter Path to the /QAanwerFiles folder
C:/Users/Admin/CMPE_297_NLP_FinalProject/QAanswerFiles/


In [28]:
# Words Count Funtion
def wordsCount(text):
    w = extracWords(text)
    return (len(w))

In [73]:
# Implementing Words Countting
start = time.time()
wordsCorpus = []    
    
ee = ['S10','S09','S08']

for Z in range(0,3):
    Sxx = str(ee[Z])
    path_AA = path + Sxx +'/data/'
    for i in range(1,(7-Z)):
        CC = 'set'+str(i)
        path_BB = (path_AA+CC+'/')
        os.chdir(path_BB)
        for filename in glob.glob("*.txt.clean"):
            sentences=[]
            doc = {}
            f = codecs.open(filename,'r','ISO-8859-1')
            file = f.read()
            len_w = wordsCount(file)
            articleFile = (Sxx+'/'+CC+'/'+filename)
            wordsCorpus.append({'articleFile':articleFile,'count':len_w,'text':file})
    
seconds = time.time() - start
print('Time Taken:', time.strftime("%H:%M:%S",time.gmtime(seconds)))

Time Taken: 00:01:11


In [74]:
wordsCorpus

[{'articleFile': 'S10/set1/a1.txt.clean',
  'count': 6193,
  'text': 'Ant\n\n\n\nAnts are social insects of the family Formicidae ( ), and along with the related wasps and bees, they belong to the order Hymenoptera. Ants evolved from wasp-like ancestors in the mid-Cretaceous period between 110 and 130 million years ago and diversified after the rise of flowering plants. Today, more than 12,500 species are classified with upper estimates of about 22,000 species.          They are easily identified by their elbowed antennae and a distinctive node-like structure that forms a slender waist.\n\nAnts form colonies that range in size from a few dozen predatory individuals living in small natural cavities to highly organised colonies which may occupy large territories and consist of millions of individuals. These larger colonies consist mostly of sterile wingless females forming castes of "workers", "soldiers", or other specialised groups. Nearly all ant colonies also have some fertile males c

### TF-IDF Supporting Functions

In [101]:
# Words Frecquencies Function:
def wordFreq(text,doc):
    freqDict={}
    words = extracWords(text)
    for word in words:
        word = word.lower()
        if word in freqDict:
            freqDict[word] += 1
        else:
            freqDict[word] = 1
    temp ={'articleFile': doc , 'freqDict': freqDict}
    return temp

# Counting Corpus Words Function
wordCountList = []
for i in wordsCorpus:
    l = wordFreq(i['text'],i['articleFile'])
    wordCountList.append(l)

# TF Calculations Function.
def calc_TF(wordsCorpus,wordCountList):
    TF_scores =[]
    for i in range(0,len(wordCountList)):
        id = wordCountList[i]['articleFile']
        for k in wordCountList[i]['freqDict']:
            temp = {'articleFile': id,
                   'TF_score': wordCountList[i]['freqDict'][k]/wordsCorpus[i]['count'],
                   'key':k}
            TF_scores.append(temp)
        i += 1
    return TF_scores

# IDF Calculation Function.
def calc_IDF(wordsCorpus,wordCountList):
    IDF_scores =[]
    for dict in wordCountList:
        id = dict['articleFile']
        for k in dict['freqDict'].keys():
            count = sum([k in tempDict['freqDict'] for tempDict in wordCountList])
            temp = {'articleFile': id,'IDF_score': math.log(len(wordsCorpus)/count),'key' : k}
            
            IDF_scores.append(temp)
    return IDF_scores

In [76]:
# TF Calulation
TF = calc_TF(wordsCorpus,wordCountList)

In [77]:
# IDF Calculation
IDF = calc_IDF(wordsCorpus,wordCountList)

In [78]:
TF_df = pd.DataFrame(TF)
IDF_df = pd.DataFrame(IDF)

In [85]:
TF_df.sample(5)

articleFile  TF_score          key
185470  S08/set3/a1.txt.clean  0.000178         feel
202995  S08/set3/a9.txt.clean  0.000561      hammond
193929  S08/set3/a5.txt.clean  0.000130      claimed
97654   S09/set1/a8.txt.clean  0.000308  angiosperms
212733  S08/set4/a7.txt.clean  0.000404   bookbinder

In [86]:
IDF_df.sample(5)

articleFile  IDF_score            key
34036   S10/set3/a4.txt.clean   1.832581     generation
162080  S08/set1/a6.txt.clean   3.218876      motivated
143343  S09/set5/a4.txt.clean   4.317488  augmentatives
16525   S10/set2/a2.txt.clean   2.066196      orchestra
68670   S10/set5/a8.txt.clean   2.813411            ipa

In [95]:
TFIDF = pd.merge(TF_df, IDF_df)
TFIDF['TFIDF_score'] = TFIDF['TF_score']*TFIDF['IDF_score']
TFIDF.head()

articleFile  TF_score       key  IDF_score  TFIDF_score
0  S10/set1/a1.txt.clean  0.019538       ant   5.010635     0.097899
1  S10/set1/a1.txt.clean  0.002584  \n\n\n\n   0.013423     0.000035
2  S10/set1/a1.txt.clean  0.034232      ants   3.624341     0.124069
3  S10/set1/a1.txt.clean  0.001938    social   0.933098     0.001808
4  S10/set1/a1.txt.clean  0.003229   insects   2.813411     0.009086

In [96]:
TFIDF.shape

(214357, 5)

In [97]:
TFIDF.set_index("key", inplace=True)
TFIDF.head()

articleFile  TF_score  IDF_score  TFIDF_score
key                                                              
ant       S10/set1/a1.txt.clean  0.019538   5.010635     0.097899
\n\n\n\n  S10/set1/a1.txt.clean  0.002584   0.013423     0.000035
ants      S10/set1/a1.txt.clean  0.034232   3.624341     0.124069
social    S10/set1/a1.txt.clean  0.001938   0.933098     0.001808
insects   S10/set1/a1.txt.clean  0.003229   2.813411     0.009086

In [100]:
# Testing TIDF For Words in Corpus.
m = "lincoln"
if m in TFIDF.index:
    print(TFIDF.loc[m])

                    articleFile  TF_score  IDF_score  TFIDF_score
key                                                              
lincoln  S10/set3/a10.txt.clean  0.000261    2.70805     0.000706
lincoln   S10/set3/a8.txt.clean  0.000582    2.70805     0.001576
lincoln   S09/set3/a4.txt.clean  0.000170    2.70805     0.000461
lincoln   S08/set2/a5.txt.clean  0.000506    2.70805     0.001370
lincoln   S08/set3/a3.txt.clean  0.001468    2.70805     0.003975
lincoln   S08/set3/a4.txt.clean  0.034373    2.70805     0.093084
lincoln   S08/set3/a5.txt.clean  0.002212    2.70805     0.005991
lincoln   S08/set3/a6.txt.clean  0.000352    2.70805     0.000953
lincoln   S08/set3/a7.txt.clean  0.001248    2.70805     0.003380
lincoln   S08/set3/a8.txt.clean  0.000150    2.70805     0.000406


----------------------------------------

# Rules Functions:

In [ ]:
# Rule Based on Lemmanized List:
def filter_R1(corpus,lemmaList):
    f_R1 = []
    for i in corpus:
        commonTerms = list(set(i['lemma']) & set(lemmaList)) 
        if len(commonTerms) > 0:
            filter1.append(i)
            
    print("Lines Filtered from filter R1------> ",len(f_R11))
    return f_R1

# Rule Based on Possitions:
def filter_R2(corpus,pos):
    f_R2 = []
    verb = []
    for i in pos:
        if i.split("_")[1] in ['VB','VBD','VBG']:
            verb.append(i.split("_")[0])
        if i.split("_")[1] in ['VBP','JJ','NN']:
            verb.append(i.split("_")[0])
    
    if "purchase" in verb:
        verb.append("buy")
    
    for i in corpus:  
        for p in i['lemma']:
            for h in verb:
                if p.split("_")[0] == h:
                    filter2.append(i)
    
    print("Lines Filtered from filter R2------> ",len(f_R2))
    return f_R2

# Rule Based on Parse Tree:
def filter_R3(corpus,q_obj):
    head_lines =[]
    for i in q_obj['parse_tree']:
        if i.split("_")[1] == "ROOT":
            head_of_question = i.split("_")[0]
    print("Head of Question ------> "+head_of_question)
    
    for i in corpus:
        for r in i['parse_tree']:
            if r.split("_")[1] == "ROOT" and r.split("_")[0] == head_of_question:
                head_lines.append(i)
                
    print("Lines Filtered from rule4_filter------> ",len(head_lines))
    return(head_lines)